In [2]:
import pandas as pd
import numpy as np
import os, sys, copy, argparse
import json
import sumolib, traci
from tqdm import tqdm
from datetime import datetime
path_root = os.path.dirname(os.path.dirname(os.path.abspath('.')))
path_scr = os.path.join(path_root, 'scripts')
sys.path.append(path_scr)
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator
self = SignalGenerator()
self.prepare_data()
self.process_history()

1. 데이터를 준비합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-5. 필요한 보조 객체들이 모두 준비되었습니다.
2. 신호이력 테이블을 변환합니다.


In [3]:
fsecs = list(range(self.present_time - self.sim_timespan, self.present_time + 1, 5))
I = len(fsecs)

In [4]:
for i in range(30): # fsec : unix time by Five SECond
    fsec = fsecs[i]
    print(f'i={i}', fsec)
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    print('1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A')
    move = pd.read_csv(os.path.join(self.path_tables, 'move', f'move_{fsec}.csv'), index_col=0).reset_index(drop=True)
    display(move)
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로번호, 종료유닉스타임)만 수집 : B
    print('2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로번호, 종료유닉스타임)만 수집 : B')
    recent_histories = [group.iloc[-1:] for _, group in self.history[self.history['end_unix'] < fsec].groupby('inter_no')] # 교차로별로 유닉스시간이 최대인 행들
    
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    display(recent_unix)
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    print('''3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
''')
    move = pd.merge(move, recent_unix, how='left', on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    display(move)
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        if isinstance(movement, pd.DataFrame): # movement가 존재할 경우 그걸 그대로 씀.
            pass
        else: 
            movement = pd.DataFrame()
    except NameError: # movement가 존재하지 않는 경우 생성
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    print('''
5. 이동류 이력정보 READ
    - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성
6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - self.subtractor // 2을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
''')
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - self.subtractor // 2을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - self.subtractor // 2].reset_index(drop=True)
    # movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)
    display(movement)

i=0 1704417900
1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A


inter_no  phas_A  phas_B  move_A  move_B
0       175       2       2       7       3
1       176       1       1       8       4
2       177       1       1       8       4
3       178       4       4       6       1
4       201       4       4       6       1
5       202       2       2      17      18
6       206       2       2      17      18
7       210       1       1       6      18

2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로번호, 종료유닉스타임)만 수집 : B


inter_no    end_unix
1867       175  1704417790
1869       176  1704417810
1866       177  1704417790
1871       178  1704417870
1870       201  1704417870
1864       202  1704417740
1868       206  1704417800
1865       210  1704417740

3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거



...

inter_no    end_unix
1876       175  1704417970
1877       176  1704417990
1875       177  1704417970
1879       178  1704418041
1878       201  1704418040
1872       202  1704417900
1874       206  1704417950
1873       210  1704417921

3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거



inter_no  phas_A  phas_B  move_A  move_B  start_unix
0       175       2       2       7       3  1704417970
1       176       3       3       5      18  1704417990
2       177       4       4       5       1  1704417970
3       178       4       4       6       1  1704418041
4       201       5       5       7       4  1704418040
5       202       2       2      17      18  1704417900
6       206       3       3       8       4  1704417950
7       210       4       4       8       3  1704417921


5. 이동류 이력정보 READ
    - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성
6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - self.subtractor // 2을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)



inter_no  phas_A  phas_B  move_A  move_B  start_unix
0        175       2       2       7       3  1704417790
1        176       1       1       8       4  1704417810
2        177       1       1       8       4  1704417790
3        178       4       4       6       1  1704417870
4        201       4       4       6       1  1704417870
5        202       2       2      17      18  1704417740
6        206       2       2      17      18  1704417800
7        210       1       1       6      18  1704417740
8        201       5       5       7       4  1704417870
9        202       2       2      17      18  1704417900
10       206       3       3       8       4  1704417800
11       175       3       3       6       1  1704417790
12       178       1       1       8       4  1704417870
13       201       1       1       8       3  1704417870
14       202       1       1       6       2  1704417900
15       210       1       2       6       2  1704417921
16       206       4       4      17      18  1704417800
17       176       2       2       8       3  1704417810
18       177       2       2       7       3  1704417790
19       175       3       4       6       2  1704417790
20       201       2       2       5       2  1704417870
21       210       2       2       5       2  1704417921
22       206       4       4      17      18  1704417950
23       177       3       3      17      18  1704417790
24       178       2       2       7       3  1704417870
25       206       1       1       8       4  1704417950
26       201       3       3       6       2  1704417870
27       175       4       4       5       2  1704417970
28       177       3       3      17      18  1704417970
29       210       3       3       7       4  1704417921
30       176       2       2       8       3  1704417990
31       206       2       2      17      18  1704417950
32       175       1       1       8       4  1704417970
33       178       3       3       5       2  1704417870
34       176       3       3       5      18  1704417990
35       177       4       4       5       1  1704417970
36       206       3       3       8       4  1704417950
37       210       4       4       8       3  1704417921
38       175       2       2       7       3  1704417970
39       178       4       4       6       1  1704418041
40       201       5       5       7       4  1704418040

In [5]:
self.make_movement()

In [6]:
self.movement

inter_no  phas_A  phas_B  move_A  move_B  start_unix
0         206       1       1       8       4  1704414620
1         206       2       2      17      18  1704414620
2         206       3       3       8       4  1704414620
3         206       4       4      17      18  1704414620
4         201       1       1       8       3  1704414640
..        ...     ...     ...     ...     ...         ...
658       178       1       1       8       4  1704418150
659       178       3       3       5       2  1704418150
660       178       4       4       6       1  1704418150
661       176       1       1       8       4  1704418180
662       176       3       3       5      18  1704418180

[663 rows x 6 columns]

In [7]:
self.update_movement()

In [9]:
self.movement_updated

inter_no  phas_A  phas_B  move_A  move_B  start_unix
0         206       1       1       8       4  1704414620
1         206       2       2      17      18  1704414620
2         206       3       3       8       4  1704414620
3         206       4       4      17      18  1704414620
4         201       1       1       8       3  1704414640
..        ...     ...     ...     ...     ...         ...
864       175       3       3       6       1  1704417790
865       175       3       4       6       2  1704417790
866       175       4       4       5       2  1704417790
867       177       1       1       8       4  1704418150
868       177       2       2      17      18  1704418150

[869 rows x 6 columns]

In [10]:
self.hrhists

inter_no  start_unix  phas_A  phas_B  duration
0        206  1704417350       1       1        45
1        206  1704417350       2       2        53
2        206  1704417350       3       3        26
3        206  1704417350       4       4        26
0        206  1704417500       1       1        45
..       ...         ...     ...     ...       ...
1        176  1704418350       2       2       103
2        176  1704418350       3       3        40
0        176  1704418530       1       1        37
1        176  1704418530       2       2       103
2        176  1704418530       3       3        40

[265 rows x 5 columns]